# Numerical bifurcation diagrams and bistable systems

Let us study the following system from [Gardner et al. (2000, Nature)](https://www.nature.com/articles/35002131):

\begin{equation}
\begin{cases}
\frac{du}{dt} = \frac{\alpha}{1+v^\beta} - u\\
\frac{dv}{dt} = \frac{\alpha}{1+u^\beta} - v
\end{cases}
\end{equation}

In [1]:
from functools import partial 
from collections import defaultdict 
import numpy as np # Numerical computing library
import matplotlib.pyplot as plt # Plotting library
import scipy.integrate #Integration library
from mpl_toolkits.mplot3d import axes3d #Used for the 3d bifurcation plot
import matplotlib.patches as mpatches #used to write custom legends
%matplotlib inline

## Trajectories 

A Cauchy problem under the form:

\begin{equation}
\begin{cases}
\frac{dy}{dt} = f(y,t)\\
y(0) = y_0
\end{cases}
\end{equation}

can be numerically solved on the interval $[0,T]$ with `scipy.integrate.odeint(f, y0, time)`. 

In [2]:
# Exercise: 
# - Simulate this system using scipy.integrate.odeint
# - Draw the trajectories using matplotlib.pyplot.plot

# We will look at those set of parameters
scenarios = [{'alpha':1, 'beta':2}, 
             {'alpha':1, 'beta':10}]

# On this timespan
time = np.linspace(0, 20, 1000)

# Here is a list of interesting initial conditions:
initial_conditions = [(.1,1), (2,2),(1,1.3),(2,3),(2,1),(1,2)]

In [3]:
def cellular_switch(y, t, alpha, beta):
    """ Flow of Gardner's bistable cellular switch
    Args:
        y (array): (concentration of u, concentration of v)
        t (float): time (not used, autonomous system)
        alpha (float): maximum rate of repressor synthesis 
        beta (float): degree of cooperative behavior.
    Return: dy/dt
    """

## Phase diagram

### Isoclines

Null isoclines are the manifolds on which one component of the flow is null. 
Find the equation of the null-isoclines for $u$ and $v$. 


In [7]:
#Exercise: 
#Plot the isoclines using matplotlib.pyplot.plot in the (u,v) plane. 

uspace = np.linspace(0,2,100)
vspace = np.linspace(0,2,100)

### Flow

The flow is a vector field of the state space that encode the local behavior of the system. 


In [9]:
# Exercise: Draw the flow using matplotlib.pyplot.streamplot

### Equilibrium points 

The equilibrium points are the root of the flow, and the intersection of two null isoclines.

In [11]:
# Exercice: Find the equation satisfied by the equilibrium points
 
# Write a function to solve an equation in the form f(x)=0
# Use scipy.optimize.fsolve, check the convergence of the numerical method 
# (use the option full_output=1 of fsolve) and return nan otherwise.  
# Use the endpoint of the trajectories as the starting points of fsolve. 

In [12]:
def findroot(func, init):
    """ Find root of equation function(x)=0
    Args:
        - the system (function),
        - the initial values (type list or np.array)

    return: correct equilibrium (type np.array) 
            if the numerical method converge or return nan
    """
    pass

def find_unique_equilibria(flow, starting_points):
    '''Return the list of unique equilibria of a flow 
    starting around starting_points'''
    pass

## Nature of the equilbirum points

The local nature and stability of the equilibrium is given by linearising the flow function. This is done using the Jacobian matrix of the flow:

\begin{equation}
\begin{bmatrix}
    F(u+h,v+k)\\G(u+h,v+k)
\end{bmatrix} =  
\begin{bmatrix}
    F(u,v)\\G(u,v)
\end{bmatrix} +
\begin{bmatrix}
    \frac{ \partial F(u,v)}{\partial u} &  \frac{ \partial F(u,v)}{\partial v}\\
    \frac{ \partial G(u,v)}{\partial u} &  \frac{ \partial G(u,v)}{\partial v}\\
\end{bmatrix}
\begin{bmatrix}
    h\\k
\end{bmatrix} + o \left( \left| \left| \begin{bmatrix}
    h\\k
\end{bmatrix} \right | \right | \right )
\end{equation}


In [15]:
# Exercise: 
#- Find the expression of the jacobian of the flow
#- Write a function to evaluate it
#- Find the stability of each equilibrium point using scipy.linalg.eigv
#- (*) Find the nature of each equilibrium point using scipy.linalg.eigv

In [16]:
def jacobian_cellular_switch(u,v, alpha, beta):
    """ Jacobian matrix of the ODE system modeling Gardner's bistable cellular switch
    Args:
        u (float): concentration of u, 
        v (float): concentration of v,
        alpha (float): maximum rate of repressor synthesis, 
        beta (float): degree of cooperative behavior.
    Return: np.array 2x2"""
    pass

def stability(jacobian):
    """ Stability of the equilibrium given its associated 2x2 jacobian matrix. 
    Args:
        jacobian (np.array 2x2): the jacobian matrix at the equilibrium point.
    Return:
        (string) status of equilibrium point.
    """
    pass 

In [21]:
# This is an utility function you can use to make your own graph prettier. 
EQUILIBRIUM_COLOR = {'Stable node':'C0',
                    'Unstable node':'C1', 
                    'Saddle':'C4',
                    'Stable focus':'C3',
                    'Unstable focus':'C2',
                    'Center (Hopf)':'C5',
                    'Transcritical (Saddle-Node)':'C6'}
def plot_equilibrium(ax, position, nature, legend=True):
    """Draw equilibrium points at position with the color 
       corresponding to their nature"""
    for pos, nat in zip(position,nature):
        ax.scatter(pos[0],pos[1],
                   color= (EQUILIBRIUM_COLOR[nat] 
                           if nat in EQUILIBRIUM_COLOR
                           else 'k'),
                   zorder=100)
        
    if legend:
        # Draw a legend for the equilibrium types that were used.
        labels = list(frozenset(nature))
        ax.legend([mpatches.Patch(color=EQUILIBRIUM_COLOR[n]) for n in labels], labels)

### Complete phase diagram

In [22]:
# Exercise: Draw on a single graph in the state space:
# - The isoclines of u and v
# - The flow 
# - The position and nature of the equilibrium points
# - The trajectories you simulated.

## Bifurcation diagram

The bifurcation diagram show the position and nature of equilibria as a function of a control parameter. In order to simplify the problem we will only plot the value of $u$ in the following.

A very naïve way of building the bifurcation diagram might be to do the procedure above for all values of beta. 


### Numerical continuation 

However, this is *not* practical for most models. We do not want to integrate the systems for all values of parameters. 

The more general problem is to solve a system of non linear equations $F(u; \lambda) = 0$ for all values of the parameter $\lambda$, knowing that the solutions are continuous with respect to $\lambda$. 

Solving by numerical approximations can be done using **Numerical continuation** methods. Here we present the simplest method called [Natural Parameter continuation](https://en.wikipedia.org/wiki/Numerical_continuation#Natural_parameter_continuation). 

In [24]:
# Exercise:
# Use Natural parameter continuation to draw the bifurcation diagram. 

# As starting points for the equilibria use the one computed for the phase
# diagram. 
# Do the continuation on: 
beta_space = np.linspace(10,0.5,1000)
starting_points = [(.5, .99), (0.84, .84), (.99, .5)]

In [25]:
def numerical_continuation(f, initial_u, lbda_values):
    """ Find the roots of the parametrised non linear equation.  
    
    Iteratively find approximate solutions of `F(u, lambda) = 0` 
    for several values of lambda. The solution of the step i is
    used as initial guess for the numerical solver at step i+1. 
    The first inital guess is initial_u (for lbda_values[0]).        
    
    Args:
        f (function): Function of u and lambda.
        initial_u (float): Starting point for the contiunation.
        lbda_values (array): Values of the parameter lambda (in the order of the continuation process).
    
    Return: 
        (numpy.array) output[i] is the solutions of f(u,lbda_values[i]) = 0
         NaN if the algorithm did not converge.
    """


In [28]:
# You can use theses for a fancy plotting. 
def get_segments(values):
    """Return a dict listing the interval where values is constant.
    Return:
        A dict mapping (start, finish) index to value"""
    start = 0
    segments = {}
    for i,val in enumerate(values[1:],1):
        if val != values[start] or i == len(values)-1:
            segments[(start,i)] = values[start]
            start = i
    return segments

def plot_bifurcation(ax, branches, lbdaspace):
    """Function to draw nice bifurcation graph
    Args:
        ax: object of the plt.subplots
        branches: a list of two lists giving the position and
        the nature of the equilibrium.
        lbda_space: bifurcation parameter space
    """
    labels = frozenset()
    for eq, nature in branches:
        labels = labels.union(frozenset(nature))
        segments = get_segments(nature)
        for idx, n in segments.items():
            ax.plot(lbdaspace[idx[0]:idx[1]],eq[idx[0]:idx[1]],
                     color=EQUILIBRIUM_COLOR[n] if n in EQUILIBRIUM_COLOR else 'k')
    ax.legend([mpatches.Patch(color=EQUILIBRIUM_COLOR[n]) for n in labels],
              labels)

## Assymetrical System

We introduce a second control parameter: now the non linearity of the inhibition is controled by $\beta_1, \beta_2$. Thus breaking the symmetry of the system as in [Ozbudak et al. 2004](https://www.nature.com/articles/nature02298): 

\begin{equation}
\begin{cases}
\frac{du}{dt} = \frac{\alpha}{1+v^{\beta_1}} - u\\
\frac{dv}{dt} = \frac{\alpha}{1+u^{\beta_2}} - v
\end{cases}
\end{equation}

In [30]:
def asymmetrical_cellular_switch(y,t,alpha, beta1, beta2):
    """Flow of the asymmetrical cellular switch model.
    Args: 
        y: (concentration of u, concentration of v)
        t: time (unused, this system is autonomous)
        alpha: maximum production of u or v
        beta1: non-linearity parameter of the effect v->u
        beta2: non-linearity parameter of the effect u->v
    Return: (np.array) [du/dt, dv/dt]
    """
    u, v = y 
    return np.array([(alpha/(1+v**beta1)) - u ,
                     (alpha/(1+u**beta2)) - v])
def jacobian_asymmetrical_cellular_switch(u,v, alpha, beta1, beta2):
    """Jacobian of the assymetrical cellular switch model.
    Args: 
        u: concentration of u
        v: concentration of v
        alpha: maximum production of u or v
        beta1: non-linearity parameter of the effect v->u
        beta2: non-linearity parameter of the effect u->v
    Return: (np.array) 2x2 Jacobian matrix. 
    """
    return - np.array([[1, alpha*beta1*v**(beta1-1) / (1+v**beta1)**2],
                       [alpha*beta2*u**(beta2-1) / (1+u**beta2)**2, 1]])

### Single parameter bifurcation 

In [31]:
# Exercise:
# We fix one of the two asymmetry parameters. Draw the phase space diagram
# for several values of the other. What do you observe ? 
# Draw the bifurcation diagram. What is the name of the bifurcation ? 
beta2 = 6.0
alpha = 1.0

# For the state space diagram you can plot the following
beta1_space = np.linspace(4, 7, 4)

# For the bifurcation diagram you can use natural parameter continuation and:
beta1_bdiag_space = np.linspace(7,0.5,1000)
starting_points = [(0.5,1), (1,0.5), (0.75,0.75)]

### The Cusp bifurcation: a bifurcation of codimension 2

We are now ready to draw the bifurcation diagram with respect to both assymetry parameters. 

In [35]:
# Plot whether the system is monostable or bistable in the 2d parameter space (beta1,beta2)
b_space = np.linspace(0, 13, 250)[1:]